In [1]:
# Cell 1: Imports and Setup
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from scipy.stats import ttest_ind
import numpy as np
from pathlib import Path
import yaml

print("Setup complete!")

# Cell 2: Load Configuration
def load_config(config_path="../../config/config.yaml"):
    """Load configuration from YAML file"""
    with open(config_path, 'r') as f:
        config = yaml.safe_load(f)
    return config

# Load configuration
config = load_config()

# Extract file paths and parameters
CN_FILE = config['files']['copy_number']
CRISPR_FILE = config['files']['crispr_scores']
DEEP_DEL_PERCENTILE = config['analysis']['deep_deletion_percentile']
SHALLOW_DEL_PERCENTILE = config['analysis']['shallow_deletion_percentile']

# Set up output directories
output_dir = Path("../../results/crispr/")
figures_dir = Path("../../figures/crispr/")
output_dir.mkdir(parents=True, exist_ok=True)
figures_dir.mkdir(parents=True, exist_ok=True)

print(f"Configuration loaded:")
print(f"  Copy number file: {CN_FILE}")
print(f"  CRISPR file: {CRISPR_FILE}")
print(f"  Deep deletion percentile: {DEEP_DEL_PERCENTILE}")
print(f"  Shallow deletion percentile: {SHALLOW_DEL_PERCENTILE}")

# Cell 3: Load and Process Data
# Load the CSV files
df1 = pd.read_csv(CN_FILE)
df2 = pd.read_csv(CRISPR_FILE)

# Calculate the average across CDK11A, CDK11B, and CCNL2 columns
df1['average_CDK11_CCNL2'] = df1[['CDK11A', 'CDK11B', 'CCNL2']].mean(axis=1)

# Define percentile thresholds for categorizing copy number
deep_del_threshold = df1['average_CDK11_CCNL2'].quantile(DEEP_DEL_PERCENTILE)
shallow_del_threshold = df1['average_CDK11_CCNL2'].quantile(SHALLOW_DEL_PERCENTILE)

print(f"Deep deletion threshold: {deep_del_threshold:.3f}")
print(f"Shallow deletion threshold: {shallow_del_threshold:.3f}")

# Categorize copy number into "Deep Deletion," "Shallow Deletion," and "Copy Neutral / Gains"
df1['CN_category'] = pd.cut(df1['average_CDK11_CCNL2'], 
                            bins=[-float('inf'), deep_del_threshold, shallow_del_threshold, float('inf')], 
                            labels=['Deep Deletion', 'Shallow Deletion', 'Copy Neutral / Gain'])

# Merge the dataframes on depmap_id
merged_df = pd.merge(df1[['depmap_id', 'CN_category']], df2, left_on='depmap_id', right_on='Depmap ID')

print(f"Merged dataframe shape: {merged_df.shape}")
print("\nCopy number distribution:")
print(merged_df['CN_category'].value_counts())

# Cell 4: Statistical Analysis
# Perform t-tests
wild_vs_shallow = ttest_ind(
    merged_df[merged_df['CN_category'] == 'Copy Neutral / Gain']['CRISPR (Project Score, CERES)'].dropna(),
    merged_df[merged_df['CN_category'] == 'Shallow Deletion']['CRISPR (Project Score, CERES)'].dropna(), 
    alternative='two-sided', equal_var=False
)
shallow_vs_deep = ttest_ind(
    merged_df[merged_df['CN_category'] == 'Shallow Deletion']['CRISPR (Project Score, CERES)'].dropna(),
    merged_df[merged_df['CN_category'] == 'Deep Deletion']['CRISPR (Project Score, CERES)'].dropna(), 
    alternative='two-sided', equal_var=False
)
wild_vs_deep = ttest_ind(
    merged_df[merged_df['CN_category'] == 'Copy Neutral / Gain']['CRISPR (Project Score, CERES)'].dropna(),
    merged_df[merged_df['CN_category'] == 'Deep Deletion']['CRISPR (Project Score, CERES)'].dropna(), 
    alternative='two-sided', equal_var=False
)

print(f"Copy Neutral vs Shallow Deletion: p = {wild_vs_shallow.pvalue:.4e}")
print(f"Shallow vs Deep Deletion: p = {shallow_vs_deep.pvalue:.4e}")
print(f"Copy Neutral vs Deep Deletion: p = {wild_vs_deep.pvalue:.4e}")

# Cell 5: Create Violin Plot
def add_stat_annotation(ax, p_value, x1, x2, y, h, star_offset=-0.2, delta_offset=-0.1, color='k'):
    ax.plot([x1, x1, x2, x2], [y, y+h, y+h, y], lw=6.5, color=color)
    if p_value < 0.001:
        star_label = '***'
    elif p_value < 0.01:
        star_label = '**'
    elif p_value < 0.05:
        star_label = '*'
    else:
        star_label = 'ns'
    ax.text((x1 + x2) * 0.5, y + h + star_offset, star_label, ha='center', va='bottom', color=color, fontsize=240)

# Set the context to increase font sizes
sns.set_context("talk", font_scale=7)

# Initialize the figure
plt.figure(figsize=(32,35), dpi=300)

custom_order = ['Copy Neutral / Gain', 'Shallow Deletion', 'Deep Deletion']

# Create violin plot
ax = sns.violinplot(x='CN_category', y='CRISPR (Project Score, CERES)', data=merged_df,
                    order=custom_order, color=".8", density_norm="count", inner='point', bw_adjust=1.5)

# Overlay scatter plot
sns.swarmplot(x='CN_category', y='CRISPR (Project Score, CERES)', data=merged_df,
              order=custom_order, color='black', size=25, ax=ax)

# Set x-ticks and labels
plt.xticks([0, 1, 2], ['Copy \n Neutral \n/ Gain', 'Shallow \nDeletion', 'Deep \nDeletion'], 
           fontsize=140, horizontalalignment='center')
ax.tick_params(axis='x', length=0, pad=15) 

ax.tick_params(axis='y', labelsize=120)
for tick in ax.get_yticklabels():
    tick.set_fontweight('bold')

# Customize plot spines
ax.spines['top'].set_visible(False)
ax.spines['right'].set_visible(False)
ax.spines['left'].set_linewidth(10)   # Left spine (y-axis)
ax.spines['bottom'].set_linewidth(10) # Bottom spine (x-axis)

# Calculate and plot the medians
means = merged_df.groupby('CN_category')['CRISPR (Project Score, CERES)'].mean().reindex(custom_order).values
for i, mean in enumerate(means):
    plt.plot(
        [i - 0.2, i + 0.2],  # Adjust the horizontal span to align with the violin width
        [mean, mean],    # Keep the y-coordinate constant at the median value
        color='red', 
        linestyle='-', 
        linewidth=12, zorder=10
    )

# Add significance annotations
y_max = merged_df['CRISPR (Project Score, CERES)'].max()

add_stat_annotation(plt.gca(), wild_vs_shallow.pvalue,  0, 1, y_max + 0.4, 0.1)
add_stat_annotation(plt.gca(), shallow_vs_deep.pvalue, 1, 2, y_max + 0.7, 0.1)
add_stat_annotation(plt.gca(), wild_vs_deep.pvalue,  0, 2, y_max + 1, 0.1)

# Add titles and labels
plt.title('CDK11: CRISPR Dependency', fontsize=180, pad=90, fontweight='bold')
plt.xlabel('Chr. 1p36 Copy Number', fontsize=180, labelpad=60, fontweight='bold')
plt.ylabel('CDK11B Dependency \nScore', fontsize=180, fontweight='bold')

# Save the plot
plt.savefig(figures_dir / 'CDK11B_CRISPR.svg', bbox_inches='tight', dpi=300, pad_inches=0.5)
plt.show()

# Cell 6: Save Results
# Save statistical results
results_df = pd.DataFrame({
    'comparison': ['Copy Neutral vs Shallow Deletion', 'Shallow vs Deep Deletion', 'Copy Neutral vs Deep Deletion'],
    'p_value': [wild_vs_shallow.pvalue, shallow_vs_deep.pvalue, wild_vs_deep.pvalue],
    'statistic': [wild_vs_shallow.statistic, shallow_vs_deep.statistic, wild_vs_deep.statistic]
})

results_df.to_csv(output_dir / 'CDK11B_CRISPR_statistics.csv', index=False)
merged_df.to_csv(output_dir / 'CDK11B_CRISPR_processed_data.csv', index=False)

print("Analysis complete!")
print(f"Results saved to: {output_dir}")
print(f"Figures saved to: {figures_dir}")

/opt/anaconda3/lib/python3.8/site-packages/pandas/core/computation/expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED


Setup complete!
Configuration loaded:
  Copy number file: ../../data/raw/crispr/1p36_CN.csv
  CRISPR file: ../../data/raw/crispr/CDK11B_CRISPR_Project_Score_CERES.csv
  Deep deletion percentile: 0.1
  Shallow deletion percentile: 0.4
Deep deletion threshold: 0.748
Shallow deletion threshold: 0.975
Merged dataframe shape: (315, 10)

Copy number distribution:
CN_category
Copy Neutral / Gain    167
Shallow Deletion       113
Deep Deletion           35
Name: count, dtype: int64
Copy Neutral vs Shallow Deletion: p = 1.8216e-10
Shallow vs Deep Deletion: p = 2.4938e-02
Copy Neutral vs Deep Deletion: p = 1.5823e-07


Analysis complete!
Results saved to: ../../results/crispr
Figures saved to: ../../figures/crispr


In [4]:
import matplotlib
import scipy 

print(f"Pandas version: {pd.__version__}")
print(f"Seaborn version: {sns.__version__}")
print(f"Matplotlib version: {matplotlib.__version__}")
print(f"SciPy version: {scipy.__version__}")
print(f"Numpy version: {np.__version__}")
print(f"PyYAML version: {yaml.__version__}")

Pandas version: 2.0.3
Seaborn version: 0.11.0
Matplotlib version: 3.7.3
SciPy version: 1.10.1
Numpy version: 1.23.0
PyYAML version: 5.3.1


In [6]:
# Cell 1: Imports and Setup
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from scipy.stats import ttest_ind
import numpy as np
from pathlib import Path
import yaml

print("Setup complete!")

# Cell 2: Load Configuration
def load_config(config_path="../../config/config.yaml"):
    """Load configuration from YAML file"""
    with open(config_path, 'r') as f:
        config = yaml.safe_load(f)
    return config

# Load configuration
config = load_config()

# Extract file paths and parameters
EXPRESSION_FILE = config['drug_sensitivity']['files']['expression']
DRUG_FILE = config['drug_sensitivity']['files']['drug_data']
LOW_EXP_PERCENTILE = config['drug_sensitivity']['analysis']['low_expression_percentile']
MEDIUM_EXP_PERCENTILE = config['drug_sensitivity']['analysis']['medium_expression_percentile']
DRUG_COLUMN = config['drug_sensitivity']['analysis']['drug_column']

# Set up output directories
output_dir = Path("../../results/drug_sensitivity/")
figures_dir = Path("../../figures/drug_sensitivity/")
output_dir.mkdir(parents=True, exist_ok=True)
figures_dir.mkdir(parents=True, exist_ok=True)

print(f"Configuration loaded:")
print(f"  Expression file: {EXPRESSION_FILE}")
print(f"  Drug file: {DRUG_FILE}")
print(f"  Low expression percentile: {LOW_EXP_PERCENTILE}")
print(f"  Medium expression percentile: {MEDIUM_EXP_PERCENTILE}")
print(f"  Drug column: {DRUG_COLUMN}")

# Cell 3: Load and Process Data
# Load the CSV files
df1 = pd.read_csv(EXPRESSION_FILE)  # Expression data
df2 = pd.read_csv(DRUG_FILE)
df2['Cell Line Name'] = df2['Cell Line Name'].apply(lambda x: x.split('_')[0] if isinstance(x, str) else x)

# Preprocess and extract average gene expression
df1['average_CDK11_CCNL2'] = df1[['CDK11A', 'CDK11B', 'CCNL2']].mean(axis=1)

# Define percentile thresholds for categorizing gene expression
low_exp_threshold = df1['average_CDK11_CCNL2'].quantile(LOW_EXP_PERCENTILE)
medium_exp_threshold = df1['average_CDK11_CCNL2'].quantile(MEDIUM_EXP_PERCENTILE)

print(f"Low expression threshold: {low_exp_threshold:.3f}")
print(f"Medium expression threshold: {medium_exp_threshold:.3f}")

# Categorize gene expression
df1['gene_exp_cat'] = pd.cut(df1['average_CDK11_CCNL2'], 
                             bins=[-float('inf'), low_exp_threshold, medium_exp_threshold, float('inf')], 
                             labels=['Low Expression', 'Medium Expression', 'High Expression'])

# Merge the two dataframes on the relevant columns
merged_df = pd.merge(df1[['cell_line_display_name', 'gene_exp_cat']], df2, 
                     left_on='cell_line_display_name', right_on='Cell Line Name')

print(f"Merged dataframe shape: {merged_df.shape}")
print("\nGene expression distribution:")
print(merged_df['gene_exp_cat'].value_counts())

# Cell 4: Statistical Analysis
# Perform t-tests
high_vs_medium = ttest_ind(
    merged_df[merged_df['gene_exp_cat'] == 'High Expression'][DRUG_COLUMN],
    merged_df[merged_df['gene_exp_cat'] == 'Medium Expression'][DRUG_COLUMN]
)
medium_vs_low = ttest_ind(
    merged_df[merged_df['gene_exp_cat'] == 'Medium Expression'][DRUG_COLUMN],
    merged_df[merged_df['gene_exp_cat'] == 'Low Expression'][DRUG_COLUMN]
)
high_vs_low = ttest_ind(
    merged_df[merged_df['gene_exp_cat'] == 'High Expression'][DRUG_COLUMN],
    merged_df[merged_df['gene_exp_cat'] == 'Low Expression'][DRUG_COLUMN]
)

print(f"High vs Medium Expression: p = {high_vs_medium.pvalue:.4e}")
print(f"Medium vs Low Expression: p = {medium_vs_low.pvalue:.4e}")
print(f"High vs Low Expression: p = {high_vs_low.pvalue:.4e}")

# Cell 5: Create Violin Plot
def add_stat_annotation(ax, p_value, delta, x1, x2, y, h, star_offset=-0.1, delta_offset=-0.6, color='k'):
    ax.plot([x1, x1, x2, x2], [y, y+h, y+h, y], lw=6.5, color=color)
    if p_value < 0.001:
        star_label = '***'
    elif p_value < 0.01:
        star_label = '**'
    elif p_value < 0.05:
        star_label = '*'
    else:
        star_label = 'ns'  # Not significant
        
    if star_label=='ns':
        ax.text((x1 + x2) * 0.5, y + h, star_label, ha='center', va='bottom', color=color, fontsize=100)
    else:
        ax.text((x1 + x2) * 0.5, y + h + star_offset, star_label, ha='center', va='bottom', color=color, fontsize=140)

    ax.text((x1 + x2) * 0.5, y + h + delta_offset, f"Δ={delta:.2f}", ha='center', va='bottom', color='black', fontsize=60)

# Set the context for increased font sizes
sns.set_context("talk", font_scale=7)

# Initialize the figure
plt.figure(figsize=(22, 32), dpi=300)

# Define the order for categories
correct_order = ['High Expression', 'Medium Expression', 'Low Expression']

# Create violin plot
ax = sns.violinplot(x='gene_exp_cat', y=DRUG_COLUMN, data=merged_df,
                    order=correct_order, color=".8", density_norm="count", inner='point', bw_adjust=1.5)

# Overlay scatter plot
sns.swarmplot(x='gene_exp_cat', y=DRUG_COLUMN, data=merged_df,
              order=correct_order, color='black', size=14, ax=ax)

# Calculate and plot the means
means = merged_df.groupby('gene_exp_cat')[DRUG_COLUMN].mean().reindex(correct_order).values
for i, mean in enumerate(means):
    plt.plot(
        [i - 0.2, i + 0.2],  # Adjust horizontal span
        [mean, mean],        # Keep y-coordinate constant at mean
        color='red', 
        linestyle='-', 
        linewidth=16, zorder=10
    )

# Customize the x-axis tick labels with the new order
plt.xticks([-0.1, 1.1, 2.3], ['High \nExp.', 'Medium \nExp.', 'Low \nExp.'], 
           fontsize=90, horizontalalignment='center')
ax.tick_params(axis='x', length=0, pad=15)

# Customize the y-axis tick labels (same as original)
ax.set_yticklabels(labels=[-1.5, -1.0, -0.5, 0.0, 0.5], fontsize=90, fontweight='bold')

# Customize plot spines
ax.spines['top'].set_visible(False)
ax.spines['right'].set_visible(False)
ax.spines['left'].set_linewidth(10)
ax.spines['bottom'].set_linewidth(10)

# Calculate deltas for annotations
delta_high_medium = means[0] - means[1]
delta_medium_low = means[1] - means[2]
delta_high_low = means[0] - means[2]

# Add significance annotations
y_max = merged_df[DRUG_COLUMN].max()

add_stat_annotation(plt.gca(), high_vs_medium.pvalue, delta_high_medium, 0, 1, y_max + 1, 0.5)
add_stat_annotation(plt.gca(), medium_vs_low.pvalue, delta_medium_low, 1, 2, y_max + 2.5, 0.5)
add_stat_annotation(plt.gca(), high_vs_low.pvalue, delta_high_low, 0, 2, y_max + 4, 0.5)

# Add titles and labels
plt.title('OTS964 Cancer Cell Line - Gene Expression Sensitivity', fontsize=120, pad=90, fontweight='bold')
plt.xlabel('Gene Expression', fontsize=120, labelpad=60, fontweight='bold')
plt.ylabel('OTS964 Log-Fold Change', fontsize=130, fontweight='bold')

# Save the plot
plt.savefig(figures_dir / 'OTS964_Gene_Exp.png', bbox_inches='tight', dpi=300, pad_inches=0.5)
plt.show()

# Cell 6: Save Results
# Save statistical results
results_df = pd.DataFrame({
    'comparison': ['High vs Medium Expression', 'Medium vs Low Expression', 'High vs Low Expression'],
    'p_value': [high_vs_medium.pvalue, medium_vs_low.pvalue, high_vs_low.pvalue],
    'statistic': [high_vs_medium.statistic, medium_vs_low.statistic, high_vs_low.statistic],
    'delta': [delta_high_medium, delta_medium_low, delta_high_low]
})

results_df.to_csv(output_dir / 'OTS964_drug_sensitivity_statistics.csv', index=False)
merged_df.to_csv(output_dir / 'OTS964_drug_sensitivity_processed_data.csv', index=False)

print("Analysis complete!")
print(f"Results saved to: {output_dir}")
print(f"Figures saved to: {figures_dir}")

Setup complete!
Configuration loaded:
  Expression file: ../../data/raw/drug_sensitivity/1p36_Expression.csv
  Drug file: ../../data/raw/drug_sensitivity/MTS023_JASON_SHELTZER_LFC_MATRIX_OTS964.csv
  Low expression percentile: 0.1
  Medium expression percentile: 0.4
  Drug column: OTS964_0.1235 uM
Low expression threshold: 4.536
Medium expression threshold: 5.202
Merged dataframe shape: (817, 11)

Gene expression distribution:
gene_exp_cat
High Expression      497
Medium Expression    247
Low Expression        73
Name: count, dtype: int64
High vs Medium Expression: p = 2.1256e-03
Medium vs Low Expression: p = 2.4776e-01
High vs Low Expression: p = 1.0733e-03


<ipython-input-6-63f7cb6487d3>:143: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_yticklabels(labels=[-1.5, -1.0, -0.5, 0.0, 0.5], fontsize=90, fontweight='bold')


Analysis complete!
Results saved to: ../../results/drug_sensitivity
Figures saved to: ../../figures/drug_sensitivity
